In [ ]:
import os
import numpy as np
import itertools
import math, random
random.seed = 42

# import torch
# from torch.utils.data import Dataset, DataLoader
# from torchvision import transforms, utils

from path import Path
import scipy.spatial.distance
import plotly.graph_objects as go
import plotly.express as px
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix

In [ ]:
"C:\\Users\\Administrator\\Documents\\akshat Project\\metadata_modelnet10.csv"

In [ ]:
folders

In [ ]:
# path = Path("../input/modelnet10-princeton-3d-object-dataset/ModelNet10")
path = Path("C:\\Users\\Administrator\\Documents\\akshat Project\\ModelNet10")

folders = [dir for dir in sorted(os.listdir(path)) if os.path.isdir(path/dir)]
classes = {folder: i for i, folder in enumerate(folders)};
classes

In [ ]:
def read_off(file):
    if 'OFF' != file.readline().strip():
        raise('Not a valid OFF header')
    n_verts, n_faces, __ = tuple([int(s) for s in file.readline().strip().split(' ')])
    verts = [[float(s) for s in file.readline().strip().split(' ')] for i_vert in range(n_verts)]
    faces = [[int(s) for s in file.readline().strip().split(' ')][1:] for i_face in range(n_faces)]
    return verts, faces


def visualize_rotate(data):
    x_eye, y_eye, z_eye = 1.25, 1.25, 0.8
    frames=[]

    def rotate_z(x, y, z, theta):
        w = x+1j*y
        return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), z

    for t in np.arange(0, 10.26, 0.1):
        xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
        frames.append(dict(layout=dict(scene=dict(camera=dict(eye=dict(x=xe, y=ye, z=ze))))))
    fig = go.Figure(data=data,
        layout=go.Layout(
            updatemenus=[dict(type='buttons',
                showactive=False,
                y=1,
                x=0.8,
                xanchor='left',
                yanchor='bottom',
                pad=dict(t=45, r=10),
                buttons=[dict(label='Play',
                    method='animate',
                    args=[None, dict(frame=dict(duration=50, redraw=True),
                        transition=dict(duration=0),
                        fromcurrent=True,
                        mode='immediate'
                        )]
                    )
                ])]
        ),
        frames=frames
    )

    return fig


def pcshow(xs,ys,zs):
    data=[go.Scatter3d(x=xs, y=ys, z=zs,
                                   mode='markers')]
    fig = visualize_rotate(data)
    fig.update_traces(marker=dict(size=2,
                      line=dict(width=2,
                      color='DarkSlateGrey')),
                      selector=dict(mode='markers'))
    fig.show()

In [62]:
df.head()

object_id    class split                    object_path
0  bathtub_0107  bathtub  test  bathtub/test/bathtub_0107.off
1  bathtub_0108  bathtub  test  bathtub/test/bathtub_0108.off
2  bathtub_0109  bathtub  test  bathtub/test/bathtub_0109.off
3  bathtub_0110  bathtub  test  bathtub/test/bathtub_0110.off
4  bathtub_0111  bathtub  test  bathtub/test/bathtub_0111.off

In [77]:
def perform_search(item, df):
    designs = df[df.loc[:,'class' ] =='bathtub'].iloc[:10, 3]
    for off in designs:
        with open(path/off, 'r') as f:
            verts, faces = read_off(f)

        i,j,k = np.array(faces).T
        x,y,z = np.array(verts).T
        len(x)
        diag = visualize_rotate([go.Mesh3d(x=x, y=y, z=z, color='yellowgreen', opacity=0.50, i=i,j=j,k=k)])
        diag.show()

In [107]:
import pandas as pd
df = pd.read_csv("C:\\Users\\Administrator\\Documents\\akshat Project\\metadata_modelnet10.csv")

In [108]:
df

object_id    class  split                    object_path
0     bathtub_0107  bathtub   test  bathtub/test/bathtub_0107.off
1     bathtub_0108  bathtub   test  bathtub/test/bathtub_0108.off
2     bathtub_0109  bathtub   test  bathtub/test/bathtub_0109.off
3     bathtub_0110  bathtub   test  bathtub/test/bathtub_0110.off
4     bathtub_0111  bathtub   test  bathtub/test/bathtub_0111.off
...            ...      ...    ...                            ...
4897   toilet_0340   toilet  train   toilet/train/toilet_0340.off
4898   toilet_0341   toilet  train   toilet/train/toilet_0341.off
4899   toilet_0342   toilet  train   toilet/train/toilet_0342.off
4900   toilet_0343   toilet  train   toilet/train/toilet_0343.off
4901   toilet_0344   toilet  train   toilet/train/toilet_0344.off

[4902 rows x 4 columns]

In [109]:
df.drop(df[df.split == 'train'].index,  inplace = True)

In [110]:
for clas in df['class'].unique():
    to_drop = df[df['class'] == clas].iloc[15:,:].index
    df.drop(to_drop, inplace=True)
df.drop(columns = 'split', axis = 1, inplace = True)

In [112]:
df.to_csv('metadata_modelnet10.csv')


In [114]:
df[df['class'] == 'bathtub']

object_id    class                    object_path
0   bathtub_0107  bathtub  bathtub/test/bathtub_0107.off
1   bathtub_0108  bathtub  bathtub/test/bathtub_0108.off
2   bathtub_0109  bathtub  bathtub/test/bathtub_0109.off
3   bathtub_0110  bathtub  bathtub/test/bathtub_0110.off
4   bathtub_0111  bathtub  bathtub/test/bathtub_0111.off
5   bathtub_0112  bathtub  bathtub/test/bathtub_0112.off
6   bathtub_0113  bathtub  bathtub/test/bathtub_0113.off
7   bathtub_0114  bathtub  bathtub/test/bathtub_0114.off
8   bathtub_0115  bathtub  bathtub/test/bathtub_0115.off
9   bathtub_0116  bathtub  bathtub/test/bathtub_0116.off
10  bathtub_0117  bathtub  bathtub/test/bathtub_0117.off
11  bathtub_0118  bathtub  bathtub/test/bathtub_0118.off
12  bathtub_0119  bathtub  bathtub/test/bathtub_0119.off
13  bathtub_0120  bathtub  bathtub/test/bathtub_0120.off
14  bathtub_0121  bathtub  bathtub/test/bathtub_0121.off